In [1]:
import numpy as np
import pandas as pd
# 导入我自定义的模块
import sys
sys.path.append("./code_libs")
import alpha_tools as at

Checking data_tools dependencies...
Checking numpy >= 1.20.3...
Find that numpy == 1.21.5...
Checking pandas >= 1.3.4...
Find that pandas == 1.3.5...
Checking bottleneck >= 1.3.4...
Find that bottleneck == 1.3.4...
Checking graphviz >= 0.20...
Find that graphviz == 0.20...
Checking scikit-learn >= 1.0.1...
Find that scikit-learn == 1.0.2...
Checking xlrd >= 2.0.1...
Find that xlrd == 2.0.1...
Checking psutil >= 5.8.0...
Find that psutil == 5.9.0...
Checking openpyxl >= 3.0.9...
Find that openpyxl == 3.0.9...
Checking xlsxwriter >= 3.0.3...
Find that xlsxwriter == 3.0.3...
Checking data_tools dependencies finished.
Checking tree_tools dependencies...
Checking numpy >= 1.20.3...
Find that numpy == 1.21.5...
Checking pandas >= 1.3.4...
Find that pandas == 1.3.5...
Checking bottleneck >= 1.3.4...
Find that bottleneck == 1.3.4...
Checking graphviz >= 0.20...
Find that graphviz == 0.20...
Checking scikit-learn >= 1.0.1...
Find that scikit-learn == 1.0.2...
Checking xlrd >= 2.0.1...
Find that

In [2]:
# 导入数据
df_ = pd.read_csv("application_record.csv")
df_response = pd.read_csv("credit_record.csv")

In [3]:
# 添加“年龄”变量
df_['Age'] = -(df_['DAYS_BIRTH']) // 365
# 定义标签
df_["target"] = df_["ID"].map(df_response.groupby("ID")["STATUS"].apply(
lambda x: 1 if ({"2", "3", "4", "5"} & set(x)) else 2 if ({"1"} & set(x)) else 0))
# 定义切片
df_['birth_year'] = df_["Age"].map(lambda x: str(2021 - x) + "0101")
df_data = df_[df_["target"].notnull()]
# 划分数据集
from sklearn.model_selection import train_test_split
df_train, df_test = train_test_split(
	df_data, test_size=0.3, stratify=df_data["target"], random_state=42)

In [4]:
# 首先定义一下之前data_flow用过的参数，便于后续直接调用
data_params = {
    "response": "target",  # 基础定义
    "split_col_name": "birth_year", "use_train_time": True,  # 时间切片
    "add_info": "ID",  # 主键添加
    "enable_single_threshold": False,  # 关闭单一值过滤
    # enable_iv_limit=True, iv_threshold=[0.01, np.inf],  # 暂不启用iv过滤
    "customized_groups": {
        "OCCUPATION_TYPE": [
            "Cleaning staff|Cooking staff|Drivers|Laborers|Low-skill Laborers|Security staff|Waiters/barmen staff",
            "Accountants|Core staff|HR staff|Medicine staff|Private service staff|Realty agents|Sales staff|Secretaries",
            "Managers|High skill tech staff|IT staff",
        ],
        "CNT_CHILDREN": [-np.inf, 0, np.inf],
    },
    "exclude_column": ["ID", "weight"],  # 排除权重
    "min_group_percent": 0,
}

In [5]:
at.Analysis.model_on_data(
    df_train, "./模型分析demo/v12/v12.xlsx", test_data=df_test,
    data_flow={
        **data_params,
        **{
            "save_or_return": False  # 跳过csv的io读写提升性能
        },
    },
    model_flow={
        # 默认流程即为评分卡建模，采用statsmodels的逻辑回归
        "model_type_path": "statsmodels.api.Logit"
    }
)

INFO Prepare kwargs...
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
INFO Prepare run...
INFO Run: DAYS_BIRTH
INFO Run: NAME_HOUSING_TYPE
INFO Run: FLAG_OWN_REALTY
INFO Run: NAME_EDUCATION_TYPE
INFO Run: CNT_FAM_MEMBERS
INFO Run: FLAG_WORK_PHONE
INFO Run: Age
INFO Run: CODE_GENDER
INFO Run: FLAG_PHONE
INFO Run: NAME_FAMILY_STATUS
INFO Run: FLAG_MOBIL
INFO Run: CNT_CHILDREN
INFO Run: NAME_INCOME_TYPE
INFO Run: OCCUPATION_TYPE
INFO Run: FLAG_EMAIL
INFO Run: DAYS_EMPLOYED
INFO Run: FLAG_OWN_CAR
INFO Run: AMT_INCOME_TOTAL
INFO Selecting...
INFO Match train: FLAG_WORK_PHONE_asC
INFO Match train: FLAG_OWN_REALTY_asD
INFO Match train: CODE_GENDER_asD
INFO Match train: Age_asC
INFO Match train: NAME_EDUCATION_TYPE_asD
INFO Match train: NAME_HOUSING_TYPE_asD
INFO Match train: DAYS_BIRTH_asC
INFO Match train: CNT_FAM_MEMBERS_asC
INFO Match train

Optimization terminated successfully.
         Current function value: 0.091927
         Iterations 8


INFO Saving train_var_stable_iv_ks...
INFO Saving train_var_stable_psi...
INFO Saving train_var_stable_quantile...
INFO Saving test_var_stable_iv_ks...
INFO Saving test_var_stable_psi...
INFO Saving test_var_stable_quantile...
INFO Saving var_stable_cross_psi...
INFO Saving var_detail...
INFO Saving var_draft...
INFO Saving var_drop...
INFO Prepare scorecard...
INFO Adding scorecard_description to excel...
INFO Converting train proba to score...
INFO Converting woe to score...
INFO Checking scorecard equation...
INFO Saving train_var_corr...
INFO Saving train vif...
INFO Getting detail score...
INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Drawing train_score_uncut_ks_graph...
INFO Drawing train_score_uncut_count_chart1...
INFO Drawing train_score_uncut_count_chart2...
INFO Drawing train_score_uncut_count_chart3...
INFO Drawing train_score_uncut_cap_chart1...
INFO Drawing train_score_uncut_cap_chart2...
INFO Drawing train_score_uncut_cap_char

In [6]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v1-lgb/v1-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v1-lgb/Data_v1-lgb.xlsx exists !
WARNING Found n_jobs n

In [7]:
at.mt.__metrics__

{'binary': {'ks': None,
  'log_loss': {'eps': 1e-15,
   'normalize': True,
   'sample_weight': None,
   'labels': None},
  'r2_score': {'sample_weight': None, 'multioutput': 'uniform_average'},
  'mean_squared_error': {'sample_weight': None,
   'multioutput': 'uniform_average'},
  'roc_auc_score': {'average': 'macro', 'sample_weight': None},
  'roc_curve': {'pos_label': None,
   'sample_weight': None,
   'drop_intermediate': True},
  'average_precision_score': {'average': 'macro', 'sample_weight': None},
  'confusion_matrix': {'labels': None, 'sample_weight': None},
  'classification_report': {'f1_formulate': <function <lambda> at 0x7f3092de4860>,
   'summary_name': ('precision', 'recall', 'f1'),
   'summary_display_func': ('max', 'mean'),
   'display_func_range': ('mean', 'max', 'min', 'std', 'sum')},
  'max_distribution_percent': None,
  'psi': None},
 'regression': {'r2_score': {'sample_weight': None,
   'multioutput': 'uniform_average'},
  'mean_squared_error': {'sample_weight': No

In [8]:
at.mt.__pattern__["model_module_path"]

('sklearn.tree',
 'sklearn.ensemble',
 'imblearn.ensemble',
 'lightgbm.sklearn',
 'lightgbm',
 'xgboost.sklearn',
 'xgboost',
 'catboost',
 'statsmodels.api',
 'sklearn.linear_model',
 'sklearn.cluster',
 'sklearn.neural_network',
 'sklearn.calibration',
 'sklearn.neighbors',
 'sklearn.isotonic',
 'sklearn.discriminant_analysis',
 'sklearn.cross_decomposition',
 'sklearn.svm',
 'sklearn.gaussian_process',
 'sklearn.mixture',
 'sklearn.naive_bayes',
 'sklearn2pmml.ensemble',
 'optional.model',
 'optional.n_model',
 'optional.d_model',
 'optional.nd_model')

In [9]:
# 默认支持缺失值的模型
at.mt.__pattern__["allow_nan"]

('xgboost.sklearn',
 'xgboost',
 'lightgbm.sklearn',
 'lightgbm',
 'optional.n_model',
 'optional.nd_model')

In [10]:
# 默认支持离散值的模型
at.mt.__pattern__["allow_discrete"]

('xgboost.sklearn',
 'xgboost',
 'lightgbm.sklearn',
 'lightgbm',
 'catboost',
 'optional.d_model',
 'optional.nd_model')

In [11]:
# 未指定填充方式时的默认填充模式
at.mt.__pattern__["default_null_mode"]

'min'

In [12]:
# train无缺失，但test存在缺失时，数值变量默认填充值
at.mt.__pattern__["nan_not_found"]

-999999

In [13]:
# train无缺失，但test存在缺失时，离散变量默认填充值
at.mt.__pattern__["null_value"]

'missing'

In [14]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v2-lr/v2-lr.xlsx", test_data=df_test,
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight", "DAYS_BIRTH"],  # 排除权重
    add_info="ID",  # 主键添加
    task_type="regression",  # 调整为 regression
    # 非分类器会自动把 convert_score 调整为 False
    model_type_path="sklearn.linear_model.LinearRegression",
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting nan_mode to min !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Find that task_type != binary, setting convert_score to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v2-lr/Data_v2-lr.xlsx exists !
INFO Selecting by corr...
INFO Total: 9...
INFO Selected: 7...
WARNING Found n_jobs not set, setting to 2 !
WARNING Setting model params: use_missing to True !
WARNING Setting model params: zero_as_missing to False !
INFO Using model params: {'max_depth': 3, 'n_estimators': 30, 'n_jobs': 2, 'use

In [15]:
at.Analysis.model_on_data(
    df_train, "./模型分析demo/v1-scorecard-more/v1-scorecard-more.xlsx",
    # 同时入参两个数据集：测试、全量
    test_data=[df_test, df_data], train_name="开发", test_names=["测试", "全量"],
    data_flow={
        **data_params,
        **{
            "save_or_return": False  # 跳过csv的io读写提升性能
        },
    },
    model_flow={
        # 默认流程即为评分卡建模，采用statsmodels的逻辑回归
        "model_type_path": "statsmodels.api.Logit"
    }
)

INFO Prepare kwargs...
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
INFO Prepare run...
INFO Run: CNT_FAM_MEMBERS
INFO Run: OCCUPATION_TYPE
INFO Run: DAYS_BIRTH
INFO Run: FLAG_OWN_REALTY
INFO Run: CODE_GENDER
INFO Run: FLAG_MOBIL
INFO Run: NAME_EDUCATION_TYPE
INFO Run: NAME_FAMILY_STATUS
INFO Run: FLAG_PHONE
INFO Run: AMT_INCOME_TOTAL
INFO Run: NAME_HOUSING_TYPE
INFO Run: Age
INFO Run: DAYS_EMPLOYED
INFO Run: NAME_INCOME_TYPE
INFO Run: FLAG_WORK_PHONE
INFO Run: FLAG_EMAIL
INFO Run: CNT_CHILDREN
INFO Run: FLAG_OWN_CAR
INFO Selecting...
INFO Match train: OCCUPATION_TYPE_asD
INFO Match train: CNT_FAM_MEMBERS_asC
INFO Match train: FLAG_OWN_REALTY_asD
INFO Match train: CODE_GENDER_asD
INFO Match train: FLAG_PHONE_asC
INFO Match train: NAME_FAMILY_STATUS_asD
INFO Match train: NAME_EDUCATION_TYPE_asD
INFO Match train: DAYS_BIRTH_asC
INFO Mat

Optimization terminated successfully.
         Current function value: 0.091927
         Iterations 8


INFO Saving var_draft...
INFO Saving var_drop...
INFO Prepare scorecard...
INFO Adding scorecard_description to excel...
INFO Converting train proba to score...
INFO Converting woe to score...
INFO Checking scorecard equation...
INFO Saving train_var_corr...
INFO Saving train vif...
INFO Getting detail score...
INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Drawing train_score_uncut_ks_graph...
INFO Drawing train_score_uncut_count_chart1...
INFO Drawing train_score_uncut_count_chart2...
INFO Drawing train_score_uncut_count_chart3...
INFO Drawing train_score_uncut_cap_chart1...
INFO Drawing train_score_uncut_cap_chart2...
INFO Drawing train_score_uncut_cap_chart3...
INFO Creating cut info...
INFO Drawing train_score_cut_ks_graph...
INFO Drawing train_score_cut_rate_chart...
INFO Drawing train_score_cut_count_chart1...
INFO Drawing train_score_cut_count_chart2...
INFO Drawing train_score_cut_count_chart3...
INFO Drawing train_score_cut_cap_chart

In [16]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v1-lgb-more/v1-lgb-more.xlsx", 
    test_data=[df_test, df_data], train_name="开发", test_names=["测试", "全量"],
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v1-lgb-more/Data_v1-lgb-more-开发-测试.xlsx exists !
WARNIN

In [17]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v3-lgb/v3-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    model_filter_order=["corr", "rank"],
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v3-lgb/Data_v3-lgb.xlsx exists !
INFO Model variables: 

In [18]:
discrete_cols = df_train.dtypes[df_train.dtypes == object].index.tolist()
at.Analysis.model_flow(
    df_train, "./模型分析demo/v4-lgb/v4-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"] + discrete_cols,  # 排除权重和离散值
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Unable to find discrete data, setting allow_discrete to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v4-lgb/Data_v4-lgb.xlsx exists !
INFO Selecting by corr...
INFO Total: 10...
INFO Selected: 7...
WARNING Found n_jobs not set, setting to 2 !
WARNING Setting model params: use_missin

In [19]:
at.mt.__pattern__["tree_default_params"]

{'max_depth': 3, 'n_estimators': 30}

In [20]:
at.Analysis.model_on_data(
    df_train, "./模型分析demo/v5-gls/v5-gls.xlsx", test_data=df_test,
    data_flow={
        **data_params,
        **{
            "save_ori": True,  # 数据集仅保留原始数据，会自动添加"ORI_"
            "save_or_return": False  # 跳过csv的io读写提升性能
        },
    },
    model_flow={
        # 更换模型，非discrete模型会自动关闭convert_score
        "model_type_path": "statsmodels.api.GLS",
        "pvalue_filter_limit": 0.5,  # 变量较少，此处调整pvalue阈值避免无变量
        # stepwise时按ORI_取值，enable_coef_negative取None跳过，check_coef_consistency取True开启
        "model_filter_order": ["corr", "stepwise"],
    }
)

INFO Prepare kwargs...
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Find that flow_data_type is ORI_, setting save_woe_data to False !
WARNING Setting format_time_edge to True !
INFO Prepare run...
INFO Run: CNT_FAM_MEMBERS
INFO Run: OCCUPATION_TYPE
INFO Run: DAYS_BIRTH
INFO Run: FLAG_OWN_REALTY
INFO Run: CODE_GENDER
INFO Run: FLAG_MOBIL
INFO Run: NAME_EDUCATION_TYPE
INFO Run: NAME_FAMILY_STATUS
INFO Run: FLAG_PHONE
INFO Run: AMT_INCOME_TOTAL
INFO Run: NAME_HOUSING_TYPE
INFO Run: Age
INFO Run: DAYS_EMPLOYED
INFO Run: NAME_INCOME_TYPE
INFO Run: FLAG_WORK_PHONE
INFO Run: FLAG_EMAIL
INFO Run: CNT_CHILDREN
INFO Run: FLAG_OWN_CAR
INFO Selecting...
INFO Match train: CODE_GENDER_asD
INFO Match train: OCCUPATION_TYPE_asD
INFO Match train: FLAG_OWN_REALTY_asD
INFO Match train: CNT_FAM_MEMBERS_asC
INFO Match train: FLAG_PHONE_asC
INFO Match train: NAME_FAMILY_STATUS_asD
INFO Mat

In [21]:
discrete_cols = df_train.dtypes[df_train.dtypes == object].index.tolist()
at.Analysis.model_flow(
    df_train, "./模型分析demo/v6-lgb/v6-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重和离散值
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    customized_variables=discrete_cols,
)

WARNING Find that recover_from_json is None and customized_variables is not empty, setting filter_variable to False !
INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that filter_variable is False, setting zero_imp_filter to False !
WARNING Find that filter_variable is False, setting enable_stepwise to False !
WARNING Find that filter_variable is False, setting enable_corr_filter to False !
WARNING Find that filter_variable is False, setting limit_var_num to inf !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find 

In [22]:
not_discrete_cols = df_train.dtypes[df_train.dtypes != object].index.tolist()
at.Analysis.model_on_data(
    df_train, "./模型分析demo/v6-lgb-oh/v6-lgb-oh.xlsx", test_data=df_test,
    data_flow={
        **data_params,
        **{
            "save_one_hot": True,  # 数据集仅保留原始数据，会自动添加"ORI_"
            "save_or_return": False,  # 跳过csv的io读写提升性能
            "exclude_column": ["ID", "weight"] + not_discrete_cols,  # 排除权重和数值变量
        },
    },
    model_flow={
        "response": "target", "split_col_name": "birth_year", "use_train_time": True,
        "exclude_column": ["ID", "weight"],  # 排除权重和离散值
        "add_info": "ID",  # 主键添加
        # 指定使用训练的class并不进行打分转化
        "model_type_path": "lightgbm.sklearn.LGBMClassifier", "convert_score": False,
        "filter_variable": False, # 数据one-hot之后变量名会变化，data_flow已经限制范围了，直接设置filter_variables能达到一样的效果
    }
)

INFO Prepare kwargs...
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Find that save_one_hot is True, setting save_woe_data to False !
WARNING Setting format_time_edge to True !
INFO Prepare run...
INFO Run: OCCUPATION_TYPE
INFO Run: NAME_HOUSING_TYPE
INFO Run: NAME_INCOME_TYPE
INFO Run: FLAG_OWN_REALTY
INFO Run: CODE_GENDER
INFO Run: NAME_EDUCATION_TYPE
INFO Run: FLAG_OWN_CAR
INFO Run: NAME_FAMILY_STATUS
INFO Selecting...
INFO Match train: CODE_GENDER_asD
INFO Match train: OCCUPATION_TYPE_asD
INFO Match train: FLAG_OWN_REALTY_asD
INFO Match train: NAME_HOUSING_TYPE_asD
INFO Match train: NAME_INCOME_TYPE_asD
INFO Match train: NAME_EDUCATION_TYPE_asD
INFO Match train: FLAG_OWN_CAR_asD
INFO Match train: NAME_FAMILY_STATUS_asD
INFO Creating train data...
INFO Creating train corr detail...
INFO Creating (-inf, 1972-01-01] corr...
INFO Creating (1972-01-01, 1984-01-01] corr..

In [23]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v7-lgb/v7-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    customized_parameter={
        "n_estimators": 200  #  默认100，尝试增加迭代次数
    }
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v7-lgb/Data_v7-lgb.xlsx exists !
WARNING Found n_jobs n

In [24]:
print(at.mt.Api.get_model_template())


        def run_logisticregression(train_data, train_response, train_all, test_all, kwargs):
            from sklearn.linear_model import LogisticRegression

            params = {}

            model_obj = template_fit_model(
                LogisticRegression, params, train_data, train_response, kwargs)


            train_p = template_use_model(model_obj, train_all, kwargs)
            test_p = template_use_model(model_obj, test_all, kwargs)

            kwargs["model_obj"] = model_obj
            return train_p, test_p, kwargs



In [25]:
def run_torch_net(train_data, train_response, train_all, test_all, kwargs):
    # 当 params = {} 时会自动使用 customized_parameter 来调参
    params = {}

    # not_discrete_cols = df_train.dtypes[df_train.dtypes != object].index.tolist()
    # num_variable = len(set(not_discrete_cols) - set(["ID", "target", "weight"]))
    # 10
    # TO DO 测试一下编译之后能不能移到后面导入
    import numpy as np
    import torch
    import torch.nn.functional as F
    from skorch import NeuralNetClassifier

    class Classifier(torch.nn.Module):
        def __init__(self):
            super(Classifier, self).__init__()
            var_num = len(train_data.columns)
            self.first_layer = torch.nn.Linear(var_num, var_num * 2)
            self.second_layer = torch.nn.Linear(var_num * 2, var_num * 4)
            self.final_layer = torch.nn.Linear(var_num * 4, 2)

        def forward(self, x_batch):
            X = self.first_layer(x_batch)
            # X = F.relu(X)
            X = torch.sigmoid(X)

            X = self.second_layer(X)
            X = torch.sigmoid(X)
            # X = F.relu(X)
            X = F.dropout(X, 0.15)

            X = self.final_layer(X)
            # X = F.relu(X)
            X = torch.sigmoid(X)
            return F.softmax(X, dim=1)

    net = NeuralNetClassifier(
        module=Classifier,
        criterion=torch.nn.CrossEntropyLoss,
        optimizer=torch.optim.Adam,
        # train_split=skorch.dataset.CVSplit(cv=5, stratified=True),
        # verbose=0,
        **params
    )
    # 使用模型函数fit拟合数据来训练模型
    net.fit(
        train_data.values.astype(np.float32),
        train_response.values.astype(np.int64)
    )
    # 通过查看 net.classes_ 来确认 p1的index的位置
    train_p = net.predict_proba(train_all.values.astype(np.float32))[:, 1]
    if test_all is not None:
        test_p = net.predict_proba(test_all.values.astype(np.float32))[:, 1]
    else:
        test_p = None
        
    # 将模型对象缓存
    kwargs["model_obj"] = net
    return train_p, test_p, kwargs

In [26]:
not_discrete_cols = df_train.dtypes[df_train.dtypes != object].index.tolist()
at.Analysis.model_flow(
    df_train, "./模型分析demo/v8-torch/v8-torch.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    model_func_definition=run_torch_net,
    customized_variables=not_discrete_cols,
    customized_parameter={
        "max_epochs": 10,
        "lr": 0.1,
    },
    precision=30,
)

WARNING Find that recover_from_json is None and customized_variables is not empty, setting filter_variable to False !
INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting nan_mode to min !
WARNING Find that filter_variable is False, setting zero_imp_filter to False !
WARNING Find that filter_variable is False, setting enable_stepwise to False !
WARNING Find that filter_variable is False, setting enable_corr_filter to False !
WARNING Find that filter_variable is False, setting limit_var_num to inf !
WARNING Find that is_stats_model is False and predict_proba not in optional.model, setting convert_score to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, 

  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4991       0.9810        0.4973  0.2400
      2        0.4972       0.9810        0.4973  0.2392
      3        0.4972       0.9810        0.4973  0.2489
      4        0.4972       0.9810        0.4973  0.2615
      5        0.4972       0.9810        0.4973  0.2437
      6        0.4972       0.9810        0.4973  0.2531
      7        0.4972       0.9810        0.4973  0.2514
      8        0.4972       0.9810        0.4973  0.2702
      9        0.4972       0.9810        0.4973  0.2569
     10        0.4972       0.9810        0.4973  0.2744


INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Drawing train_score_uncut_ks_graph...
INFO Drawing train_score_uncut_count_chart1...
INFO Drawing train_score_uncut_count_chart2...
INFO Drawing train_score_uncut_count_chart3...
INFO Drawing train_score_uncut_cap_chart1...
INFO Drawing train_score_uncut_cap_chart2...
INFO Drawing train_score_uncut_cap_chart3...
INFO Creating cut info...
INFO Drawing train_score_cut_ks_graph...
INFO Drawing train_score_cut_rate_chart...
INFO Drawing train_score_cut_count_chart1...
INFO Drawing train_score_cut_count_chart2...
INFO Drawing train_score_cut_count_chart3...
INFO Drawing train_score_cut_cap_chart1...
INFO Drawing train_score_cut_cap_chart2...
INFO Drawing train_score_cut_cap_chart3...
INFO Creating qcut info...
INFO Drawing train_score_qcut_ks_graph...
INFO Drawing train_score_qcut_rate_chart...
INFO Drawing train_score_qcut_count_chart1...
INFO Drawing train_score_qcut_count_chart2...
INFO Drawing trai

  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4989       0.9817        0.4970  0.1679
      2        0.4970       0.9817        0.4970  0.1797
      3        0.4970       0.9817        0.4970  0.1739
      4        0.4970       0.9817        0.4970  0.1720
      5        0.4970       0.9817        0.4970  0.1698
      6        0.4970       0.9817        0.4970  0.1675
      7        0.4970       0.9817        0.4970  0.1825
      8        0.4970       0.9817        0.4970  0.1662
      9        0.4970       0.9817        0.4970  0.1611
     10        0.4970       0.9817        0.4970  0.1635


INFO Saving train results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-based psi...
INFO Calculating Equivalent-based psi...


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4994       0.9802        0.4977  0.1714
      2        0.4977       0.9802        0.4977  0.1707
      3        0.4977       0.9802        0.4977  0.1800
      4        0.4977       0.9802        0.4977  0.1791
      5        0.4977       0.9802        0.4977  0.1775
      6        0.4977       0.9802        0.4977  0.1728
      7        0.4977       0.9802        0.4977  0.1806
      8        0.4977       0.9802        0.4977  0.1689
      9        0.4977       0.9802        0.4977  0.1694
     10        0.4977       0.9802        0.4977  0.1742


INFO Saving train results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-based psi...
INFO Calculating Equivalent-based psi...


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4998       0.9819        0.4969  0.1673
      2        0.4970       0.9819        0.4969  0.1665
      3        0.4970       0.9819        0.4969  0.1741
      4        0.4970       0.9819        0.4969  0.1767
      5        0.4970       0.9819        0.4969  0.1719
      6        0.4970       0.9819        0.4969  0.1734
      7        0.4970       0.9819        0.4969  0.1706
      8        0.4970       0.9819        0.4969  0.1721
      9        0.4970       0.9819        0.4969  0.1737
     10        0.4970       0.9819        0.4969  0.1817


INFO Saving train results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-based psi...
INFO Calculating Equivalent-based psi...
INFO Saving cross validate...
INFO Drawing cv compare graph...
INFO Drawing cv_compare_ks_chart...
INFO Drawing cv_compare_auc_chart...
INFO Drawing cv_compare_ap_chart...
INFO Drawing cv_compare_logloss_chart...
INFO Drawing cv_compare_r2_char

In [27]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v9-lgb/v9-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    customized_parameter={
        "n_estimators": [10, 20, 30, 40, 50],
        "learning_rate": [0.05, 0.08, 0.10]
    }
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that model_search_method not in (order, order-random), setting auto_search_loop to 1 !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional fl

In [28]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v10-lgb/v10-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    customized_parameter={
        "n_estimators": [10, 20, 30, 40, 50],
        "learning_rate": [0.05, 0.08, 0.10]
    },
    model_search_target={"binary": "ks"},
    model_search_params={"binary": ["max", -1]},
    sample_weight_name="weight",
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that model_search_method not in (order, order-random), setting auto_search_loop to 1 !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional fl

In [29]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v11-lgb/v11-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    customized_parameter={
        "n_estimators": list(range(5, 200, 10)),
        "learning_rate": [i/100 for i in range(5, 15, 1)],
    }
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that model_search_method not in (order, order-random), setting auto_search_loop to 1 !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional fl

In [30]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v12-lgb/v12-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    customized_parameter={
        "n_estimators": list(range(5, 200, 10)),
        "learning_rate": [i/100 for i in range(5, 15, 1)],
        "max_depth": [3, 4, 5, -1],
        "min_child_samples": list(range(20, 55, 5)),
        "min_child_weight": [i/1000 for i in range(1, 11, 1)],
    },
    model_search_method="order",
    model_search_params={"binary": ["max", -1]}
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v12-lgb/Data_v12-lgb.xlsx exists !
WARNING Found n_jobs

In [31]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v13-lgb/v13-lgb.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="lightgbm.sklearn.LGBMClassifier",
    convert_score=False,
    customized_parameter={
        "n_estimators": list(range(5, 200, 10)),
        "learning_rate": [i/100 for i in range(5, 15, 1)],
        "max_depth": [3, 4, 5, -1],
        "min_child_samples": list(range(20, 55, 5)),
        "min_child_weight": [i/1000 for i in range(1, 11, 1)],
    },
    model_search_method="random",
    model_search_params={"binary": ["max", -1]},
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_stepwise to False !
WARNING Find that allow_nan is True or allow_discrete is True, setting enable_corr_filter to False !
WARNING Find that model_search_method not in (order, order-random), setting auto_search_loop to 1 !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional fl

In [32]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/v14-knn/v14-knn.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    # 指定使用训练的class并不进行打分转化
    model_type_path="sklearn.neighbors.KNeighborsClassifier",
    convert_score=False,
    customized_parameter={
        "n_neighbors": [3, 4, 5, 6, 7, 8],
        "weights": ['uniform', 'distance'],
        "leaf_size": [20, 30, 40, 50],
    },
    model_search_method="tpe",
    model_search_params={"binary": ["max", -1]},
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting nan_mode to min !
WARNING Pre: WOE_ not found, change pre to "" !
WARNING Find that model_search_method not in (order, order-random), setting auto_search_loop to 1 !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/v14-knn/Data_v14-knn.xlsx exists !
INFO Selecting by corr...
INFO Total: 10...
INFO Selected: 7...
WARNING Found n_jobs not set, setting to 2 !
WARNING Setting model params: use_missing to True !
WARNING Setting model params: zero_as_missing to False !
INFO Using model params: {'max_depth': 3, 'n_e

  0%|          | 0/36 [00:00<?, ?trial/s, best loss=?]

INFO build_posterior_wrapper took 0.001021 seconds
INFO TPE using 0 trials
INFO ALL params: {'n_neighbors': 6, 'weights': 'distance', 'leaf_size': 41}...
INFO birth_year | 3 | cv flow...
WARNING Found n_jobs not set, setting to 2 !
INFO Using model params: {'n_neighbors': 6, 'weights': 'distance', 'leaf_size': 41, 'n_jobs': 2}
INFO Using variables: 6...
INFO Training KNeighborsClassifier...
INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-based psi...
INFO Calculating

  3%|▎         | 1/36 [00:01<00:57,  1.65s/trial, best loss: -0.9808088067603966]

INFO build_posterior_wrapper took 0.001112 seconds
INFO TPE using 1/1 trials with best loss -0.980809
INFO ALL params: {'n_neighbors': 6, 'weights': 'uniform', 'leaf_size': 27}...
INFO birth_year | 3 | cv flow...
WARNING Found n_jobs not set, setting to 2 !
INFO Using model params: {'n_neighbors': 6, 'weights': 'uniform', 'leaf_size': 27, 'n_jobs': 2}
INFO Using variables: 6...
INFO Training KNeighborsClassifier...
INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-base

...

100%|██████████| 36/36 [00:49<00:00,  1.38s/trial, best loss: -0.9879391514987147]

INFO Drawing cv search graph...
INFO Drawing params_search_chart...
WARNING Found n_jobs not set, setting to 2 !
INFO Using model params: {'leaf_size': 36, 'n_neighbors': 8, 'weights': 'distance', 'n_jobs': 2}
INFO Using variables: 6...
INFO Training KNeighborsClassifier...
INFO [FIT_TRANSFORM] ['AMT_INCOME_TOTAL']: 0.001133 secs
INFO [FIT_TRANSFORM] ['Age']: 0.000281 secs
INFO [FIT_TRANSFORM] ['CNT_CHILDREN']: 0.000213 secs
INFO [FIT_TRANSFORM] ['DAYS_EMPLOYED']: 0.000251 secs
INFO [FIT_TRANSFORM] ['FLAG_PHONE']: 0.000283 secs
INFO [FIT_TRANSFORM] ['FLAG_WORK_PHONE']: 0.000245 secs
INFO [TRANSFORM] ['AMT_INCOME_TOTAL']: 0.000303 secs
INFO [TRANSFORM] ['Age']: 0.001819 secs
INFO [TRANSFORM] ['CNT_CHILDREN']: 0.000626 secs
INFO [TRANSFORM] ['DAYS_EMPLOYED']: 0.00062 secs
INFO [TRANSFORM] ['FLAG_PHONE']: 0.00053 secs
INFO [TRANSFORM] ['FLAG_WORK_PHONE']: 0.000165 secs


INFO [TRANSFORM] ['AMT_INCOME_TOTAL']: 0.000265 secs
INFO [TRANSFORM] ['Age']: 0.001023 secs
INFO [TRANSFORM] ['CNT_CHILDREN']: 0.000141 secs
INFO [TRANSFORM] ['DAYS_EMPLOYED']: 0.000131 secs
INFO [TRANSFORM] ['FLAG_PHONE']: 0.000137 secs
INFO [TRANSFORM] ['FLAG_WORK_PHONE']: 0.000135 secs
INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Drawing train_score_uncut_ks_graph...
INFO Drawing train_score_uncut_count_chart1...
INFO Drawing train_score_uncut_count_chart2...
INFO Drawing train_score_uncut_count_chart3...
INFO Drawing train_score_uncut_cap_chart1...
INFO Drawing train_score_uncut_cap_chart2...
INFO Drawing train_score_uncut_cap_chart3...
INFO Creating cut info...
INFO Drawing train_score_cut_ks_graph...
INFO Drawing train_score_cut_rate_chart...
INFO Drawing train_score_cut_count_chart1...
INFO Drawing train_score_cut_count_chart2...
INFO Drawing train_score_cut_count_chart3...
INFO Drawing train_score_cut_cap_chart1...
INFO Drawing trai

Standard output is empty
Standard error:
Apr 12, 2022 4:34:52 PM org.jpmml.sklearn.Main run
INFO: Parsing PKL..
Apr 12, 2022 4:34:52 PM org.jpmml.sklearn.Main run
SEVERE: Failed to parse PKL
net.razorvine.pickle.PickleException: expected zero arguments for construction of ClassDict (for sklearn.metrics._dist_metrics.newObj). This happens when an unsupported/unregistered class is being unpickled that requires construction arguments. Fix it by registering a custom IObjectConstructor for this class.
	at net.razorvine.pickle.objects.ClassDictConstructor.construct(ClassDictConstructor.java:23)
	at net.razorvine.pickle.Unpickler.load_reduce(Unpickler.java:759)
	at net.razorvine.pickle.Unpickler.dispatch(Unpickler.java:199)
	at org.jpmml.python.PickleUtil$1.dispatch(PickleUtil.java:83)
	at net.razorvine.pickle.Unpickler.load(Unpickler.java:109)
	at org.jpmml.python.PickleUtil.unpickle(PickleUtil.java:104)
	at org.jpmml.sklearn.Main.run(Main.java:155)
	at org.jpmml.sklearn.Main.main(Main.java:

INFO Total: 64.64 s
INFO Total: 64.69 s


In [33]:
df_train, df_test = df_train.copy(), df_test.copy()
df_train["Age-swap"], df_test["Age-swap"] = df_train["Age"].copy(), df_test["Age"].copy()
df_train["sample1"] = np.random.rand(df_train.index.size)
df_train["sample2"] = np.random.uniform(0, 1, df_train.index.size)
df_test["sample1"] = np.random.rand(df_test.index.size)
df_test["sample2"] = np.random.uniform(0, 1, df_test.index.size)
at.Analysis.model_on_data(
    df_train, "./模型分析demo/v15/v15.xlsx", test_data=df_test,
    data_flow={
        **data_params, **{
            "save_or_return": False,  # 跳过csv的io读写提升性能
            "add_info": ["ID", "sample1", "sample2", "Age-swap"],  # model_flow才能读到
        },
    },
    model_flow={
        "split_col_name": "birth_year", "use_train_time": True,
        "exclude_column": ["ID", "weight"],  # 排除权重
        "swap_compare_name": ["sample1", "sample2", "Age-swap"],  # 直接伪造数据假设有三列需要swap
    }
)

INFO Prepare kwargs...
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting format_time_edge to True !
INFO Prepare run...
INFO Run: CNT_FAM_MEMBERS
INFO Run: OCCUPATION_TYPE
INFO Run: FLAG_PHONE
INFO Run: AMT_INCOME_TOTAL
INFO Run: NAME_HOUSING_TYPE
INFO Run: Age
INFO Run: DAYS_BIRTH
INFO Run: DAYS_EMPLOYED
INFO Run: NAME_INCOME_TYPE
INFO Run: FLAG_WORK_PHONE
INFO Run: FLAG_OWN_REALTY
INFO Run: CODE_GENDER
INFO Run: FLAG_MOBIL
INFO Run: CNT_CHILDREN
INFO Run: FLAG_EMAIL
INFO Run: NAME_EDUCATION_TYPE
INFO Run: FLAG_OWN_CAR
INFO Run: NAME_FAMILY_STATUS
INFO Selecting...
INFO Match train: FLAG_PHONE_asC
INFO Match train: OCCUPATION_TYPE_asD
INFO Match train: CNT_FAM_MEMBERS_asC
INFO Match train: NAME_HOUSING_TYPE_asD
INFO Match train: FLAG_OWN_REALTY_asD
INFO Match train: NAME_INCOME_TYPE_asD
INFO Match train: FLAG_WORK_PHONE_asC
INFO Match train: AMT_INCOME_TOTAL_asC
IN

Optimization terminated successfully.
         Current function value: 0.091927
         Iterations 8


INFO Saving var_drop...
INFO Prepare scorecard...
INFO Adding scorecard_description to excel...
INFO Converting train proba to score...
INFO Converting woe to score...
INFO Checking scorecard equation...
INFO Saving train_var_corr...
INFO Saving train vif...
INFO Getting detail score...
INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Drawing train_score_uncut_ks_graph...
INFO Drawing train_score_uncut_count_chart1...
INFO Drawing train_score_uncut_count_chart2...
INFO Drawing train_score_uncut_count_chart3...
INFO Drawing train_score_uncut_cap_chart1...
INFO Drawing train_score_uncut_cap_chart2...
INFO Drawing train_score_uncut_cap_chart3...
INFO Creating cut info...
INFO Drawing train_score_cut_ks_graph...
INFO Drawing train_score_cut_rate_chart...
INFO Drawing train_score_cut_count_chart1...
INFO Drawing train_score_cut_count_chart2...
INFO Drawing train_score_cut_count_chart3...
INFO Drawing train_score_cut_cap_chart1...
INFO Drawing train_s

In [34]:
df_train, df_test = df_train.copy(), df_test.copy()
df_train["sample1"] = np.random.rand(df_train.index.size)
df_train["sample2"] = np.random.uniform(0, 1, df_train.index.size)
df_test["sample1"] = np.random.rand(df_test.index.size)
df_test["sample2"] = np.random.uniform(0, 1, df_test.index.size)
at.Analysis.model_flow(
    df_train, "./模型分析demo/v16/v16.xlsx", test_data=df_test, 
    # 目标定义 & 切片定义
    response="target", split_col_name="birth_year", use_train_time=True,
    exclude_column=["ID", "weight"],  # 排除权重
    add_info="ID",  # 主键添加
    exists_proba_name="Age",  # 假设此处Age是需要进行评估的模型结果
    swap_compare_name=["sample1", "sample2"],  # 直接伪造数据假设这两个维度需要swap
)

INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting nan_mode to min !
WARNING Find that exists_proba_name is int, setting convert_score to False, setting precision to 0 !
WARNING Find that convert_score is False, setting keep_raw_score to False !
WARNING Find that convert_score is False, setting save_score_desc to False !
WARNING Find that convert_score is False, setting save_score_pmml to False !
INFO Model optional flow...
INFO Saving train results...
INFO Getting total score...
INFO Creating uncut info...
INFO Drawing train_score_uncut_ks_graph...
INFO Drawing train_score_uncut_count_chart1...
INFO Drawing train_score_uncut_count_chart2...
INFO Drawing train_score_uncut_count_chart3...
INFO Drawing train_score_uncut_cap_chart1...
INFO Drawing train_score_uncut_cap_chart2...
INFO Drawing train_score_u

In [35]:
df_train.drop(["sample1", "sample2", "Age-swap"], axis=1, inplace=True)
df_test.drop(["sample1", "sample2", "Age-swap"], axis=1, inplace=True)

In [36]:
at.Analysis.model_flow(
    df_train, "./模型分析demo/vr-torch/vr-torch.xlsx", test_data=df_test, 
    recover_from_json="./模型分析demo/v8-torch/Model_v8-torch.json"
)

WARNING /home/conda_env/模型分析demo/v8-torch/Model_v8-torch_model.pkl not exists, setting recover_from_pkl to False !
INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Find that filter_variable is False, setting zero_imp_filter to False !
WARNING Find that filter_variable is False, setting enable_stepwise to False !
WARNING Find that filter_variable is False, setting enable_corr_filter to False !
WARNING Find that filter_variable is False, setting limit_var_num to inf !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/vr-torch/Data_vr-torch.xlsx exists !
INFO Model variables: ['CNT_CHILDREN', 'AMT_INCOME_TOTAL', 'DAYS_BIRTH', 'DAYS_EMPLOYED', 'FLAG_MOBIL', 'FLAG_WORK_PHONE', 'FLAG_PHONE', 'FLAG_EMAIL', 'CNT_FAM_MEMBERS', 'Age'] !


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4989       0.9810        0.4973  0.2592
      2        0.4972       0.9810        0.4973  0.3054
      3        0.4972       0.9810        0.4973  0.2572
      4        0.4972       0.9810        0.4973  0.2506
      5        0.4972       0.9810        0.4973  0.2443
      6        0.4972       0.9810        0.4973  0.2531
      7        0.4972       0.9810        0.4973  0.2538
      8        0.4972       0.9810        0.4973  0.2563
      9        0.4972       0.9810        0.4973  0.2560
     10        0.4972       0.9810        0.4973  0.2589


INFO Saving train results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Drawing train_score_uncut_ks_graph...
INFO Drawing train_score_uncut_count_chart1...
INFO Drawing train_score_uncut_count_chart2...
INFO Drawing train_score_uncut_count_chart3...
INFO Drawing train_score_uncut_cap_chart1...
INFO Drawing train_score_uncut_cap_chart2...
INFO Drawing train_score_uncut_cap_chart3...
INFO Creating cut info...
INFO Drawing train_score_cut_ks_graph...
INFO Drawing train_score_cut_rate_chart...
INFO Drawing train_score_cut_count_chart1...
INFO Drawing train_score_cut_count_chart2...
INFO Drawing train_score_cut_count_chart3...
INFO Drawing train_score_cut_cap_chart1...
INFO Drawing train_score_cut_cap_chart2...
INFO Drawing train_score_cut_cap_chart3...
INFO Creating qcut info...
INFO Drawing train_score_qcut_ks_graph...
INFO Drawing train_score_qcu

  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4992       0.9817        0.4970  0.1657
      2        0.4970       0.9817        0.4970  0.1685
      3        0.4970       0.9817        0.4970  0.1672
      4        0.4970       0.9817        0.4970  0.1691
      5        0.4970       0.9817        0.4970  0.1616
      6        0.4970       0.9817        0.4970  0.1653
      7        0.4970       0.9817        0.4970  0.1598
      8        0.4970       0.9817        0.4970  0.1670
      9        0.4970       0.9817        0.4970  0.1644
     10        0.4970       0.9817        0.4970  0.1693


INFO Saving train results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-based psi...
INFO Calculating Equivalent-based psi...


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.5000       0.9802        0.4977  0.1647
      2        0.4977       0.9802        0.4977  0.1658
      3        0.4977       0.9802        0.4977  0.1669
      4        0.4977       0.9802        0.4977  0.1750
      5        0.4977       0.9802        0.4977  0.1742
      6        0.4977       0.9802        0.4977  0.1668
      7        0.4977       0.9802        0.4977  0.1649
      8        0.4977       0.9802        0.4977  0.1798
      9        0.4977       0.9802        0.4977  0.1790
     10        0.4977       0.9802        0.4977  0.1672


INFO Saving train results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-based psi...
INFO Calculating Equivalent-based psi...


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4991       0.9819        0.4969  0.1718
      2        0.4970       0.9819        0.4969  0.1863
      3        0.4970       0.9819        0.4969  0.1714
      4        0.4970       0.9819        0.4969  0.1894
      5        0.4970       0.9819        0.4969  0.1676
      6        0.4970       0.9819        0.4969  0.1729
      7        0.4970       0.9819        0.4969  0.1940
      8        0.4970       0.9819        0.4969  0.1806
      9        0.4970       0.9819        0.4969  0.1756
     10        0.4970       0.9819        0.4969  0.2019


INFO Saving train results...
INFO Getting total score...
WARNING Find that auto_resize_score is True and np.corrcoef(target, proba)[0, 1] < 0, replace proba with 100 / (proba + 1) !
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Saving test results...
INFO Getting total score...
INFO Creating uncut info...
INFO Creating cut info...
INFO Creating qcut info...
INFO Creating precision recall fscore...
INFO Creating results summary...
INFO Calculating Equidistant-based psi...
INFO Calculating Equivalent-based psi...
INFO Saving cross validate...
INFO Drawing cv compare graph...
INFO Drawing cv_compare_ks_chart...
INFO Drawing cv_compare_auc_chart...
INFO Drawing cv_compare_ap_chart...
INFO Drawing cv_compare_logloss_chart...
INFO Drawing cv_compare_r2_chart...
INFO Drawing cv_compare_mse_chart...
INFO Drawing cv_compare_mdp_chart...
INFO Drawing cv_compare_psi_chart...
INFO Draw

In [37]:
ori_name = "./模型分析demo/v4-lgb/v4-lgb.xlsx"
new_output = "./模型分析demo/vr-lgb/vr-lgb.xlsx"
at.Analysis.model_flow(
    df_train, new_output,
    test_data=[df_test, df_data], train_name="开发", test_names=["测试", "全量"],
    recover_path=ori_name, 
    # 继承 v4 并进行参数搜索，映射到多个数据集
    customized_parameter={
        "n_estimators": [10, 20, 30, 40, 50],
        "learning_rate": [0.05, 0.08, 0.10]
    }
)

WARNING Overwriting: customized_parameter found, disable recover from pkl !
WARNING Overwriting found, setting recover_from_pkl to False !
INFO Prepare kwargs...
WARNING Setting format_time_edge to True !
INFO Checking train_data...
INFO Checking response...
INFO Checking test_data...
INFO Checking response...
INFO Checking columns...
INFO Checking dtypes...
WARNING Setting allow_nan to True by lightgbm.sklearn !
WARNING Setting allow_discrete to True by lightgbm.sklearn !
WARNING Unable to find nan data, setting allow_nan to False !
WARNING Unable to find discrete data, setting allow_discrete to False !
INFO Model optional flow...
WARNING Check /home/conda_env/模型分析demo/vr-lgb/Data_vr-lgb-开发-测试.xlsx exists !
INFO Model variables: ['AMT_INCOME_TOTAL', 'Age', 'CNT_CHILDREN', 'DAYS_EMPLOYED', 'FLAG_PHONE', 'FLAG_WORK_PHONE'] !
WARNING Found n_jobs not set, setting to 2 !
WARNING Setting model params: use_missing to True !
WARNING Setting model params: zero_as_missing to False !
INFO Using

In [38]:
at.dt.Api.zip_dir_files("./模型分析demo/vr-lgb.zip", "./模型分析demo/vr-lgb")

INFO Saving ./模型分析demo/vr-lgb/Model_vr-lgb-开发-测试.xlsx...
INFO Saving ./模型分析demo/vr-lgb/Model_vr-lgb-开发-测试.json...
INFO Saving ./模型分析demo/vr-lgb/Model_vr-lgb-开发-测试_model.pkl...
INFO Saving ./模型分析demo/vr-lgb/Model_vr-lgb-开发-全量.json...
INFO Saving ./模型分析demo/vr-lgb/Model_vr-lgb-开发-全量_model.pkl...
INFO Saving ./模型分析demo/vr-lgb/Model_vr-lgb-开发-全量.xlsx...


In [39]:
help(at.Report.create_model_report)

Help on function in module alpha_tools:

create_model_report(new_excel_name, excel_path_list, excel_name_list, train_test_dir_cn=None)
    Usage:
    ---------
    create_model_report(
        "xxx.xlsx", [
            "file1.xlsx", "file2.xlsx", ...
        ], [
            "filename1", "filename2", ...
        ], ["train_display_name", "test_display_name"]
    )
    ---------



In [40]:
help(at.Report.create_model_report2)

Help on function in module alpha_tools:

create_model_report2(new_excel_name, output_name, train_name, test_names)
    Usage:
    ---------
    Example1:
    ---------
    create_model_report2(
        "xxx.xlsx", "report.xlsx", "train", ["test1", "test2", ...]
    )
    ---------
    Example2:
    ---------
    create_model_report2(
        "xxx.xlsx", {
            "name1": "report1.xlsx",
            "name2": "report2.xlsx",
            ...
        }, "train", ["test1", "test2", ...]
    )
    ---------



In [41]:
at.Report.create_model_report(
    "./模型分析demo/vm-模型对比/vm-模型对比.xlsx",
    [
        "./模型分析demo/v1-lgb/v1-lgb.xlsx", "./模型分析demo/v2-lr/v2-lr.xlsx",
        "./模型分析demo/v3-lgb/v3-lgb.xlsx", "./模型分析demo/v4-lgb/v4-lgb.xlsx",
        "./模型分析demo/v5-gls/v5-gls.xlsx", "./模型分析demo/v6-lgb/v6-lgb.xlsx",
        "./模型分析demo/v6-lgb-oh/v6-lgb-oh.xlsx", "./模型分析demo/v7-lgb/v7-lgb.xlsx",
        "./模型分析demo/v8-torch/v8-torch.xlsx", "./模型分析demo/v9-lgb/v9-lgb.xlsx",
        "./模型分析demo/v10-lgb/v10-lgb.xlsx", "./模型分析demo/v11-lgb/v11-lgb.xlsx",
        "./模型分析demo/v12-lgb/v12-lgb.xlsx", "./模型分析demo/v13-lgb/v13-lgb.xlsx",
        "./模型分析demo/v14-knn/v14-knn.xlsx",        
    ], [
        "v1-lgb", "v2-lr", "v3-lgb", "v4-lgb", "v5-gls",
        "v6-lgb", "v6-lgb-oh", "v7-lgb", "v8-torch", "v9-lgb",
        "v10-lgb", "v11-lgb", "v12-lgb", "v13-lgb", "v14-knn",
    ]
)

INFO Loading ./模型分析demo/v1-lgb/Model_v1-lgb.xlsx...
INFO Loading ./模型分析demo/v2-lr/Model_v2-lr.xlsx...
INFO Loading ./模型分析demo/v3-lgb/Model_v3-lgb.xlsx...
INFO Loading ./模型分析demo/v4-lgb/Model_v4-lgb.xlsx...
INFO Loading ./模型分析demo/v5-gls/Model_v5-gls.xlsx...
INFO Loading ./模型分析demo/v6-lgb/Model_v6-lgb.xlsx...
INFO Loading ./模型分析demo/v6-lgb-oh/Model_v6-lgb-oh.xlsx...
INFO Loading ./模型分析demo/v7-lgb/Model_v7-lgb.xlsx...
INFO Loading ./模型分析demo/v8-torch/Model_v8-torch.xlsx...
INFO Loading ./模型分析demo/v9-lgb/Model_v9-lgb.xlsx...
INFO Loading ./模型分析demo/v10-lgb/Model_v10-lgb.xlsx...
INFO Loading ./模型分析demo/v11-lgb/Model_v11-lgb.xlsx...
INFO Loading ./模型分析demo/v12-lgb/Model_v12-lgb.xlsx...
INFO Loading ./模型分析demo/v13-lgb/Model_v13-lgb.xlsx...
INFO Loading ./模型分析demo/v14-knn/Model_v14-knn.xlsx...
INFO Creating books summary...
INFO Saving...
INFO Creating 模型评估-变量参数-v1-lgb...
INFO Creating 模型评估-变量参数-v2-lr...
INFO Creating 模型评估-变量参数-v3-lgb...
INFO Creating 模型评估-变量参数-v4-lgb...
INFO Creating 模型评估-变量

(['./模型分析demo/v1-lgb/v1-lgb.xlsx',
  './模型分析demo/v2-lr/v2-lr.xlsx',
  './模型分析demo/v3-lgb/v3-lgb.xlsx',
  './模型分析demo/v4-lgb/v4-lgb.xlsx',
  './模型分析demo/v5-gls/v5-gls.xlsx',
  './模型分析demo/v6-lgb/v6-lgb.xlsx',
  './模型分析demo/v6-lgb-oh/v6-lgb-oh.xlsx',
  './模型分析demo/v7-lgb/v7-lgb.xlsx',
  './模型分析demo/v8-torch/v8-torch.xlsx',
  './模型分析demo/v9-lgb/v9-lgb.xlsx',
  './模型分析demo/v10-lgb/v10-lgb.xlsx',
  './模型分析demo/v11-lgb/v11-lgb.xlsx',
  './模型分析demo/v12-lgb/v12-lgb.xlsx',
  './模型分析demo/v13-lgb/v13-lgb.xlsx',
  './模型分析demo/v14-knn/v14-knn.xlsx'],
 ['v1-lgb',
  'v2-lr',
  'v3-lgb',
  'v4-lgb',
  'v5-gls',
  'v6-lgb',
  'v6-lgb-oh',
  'v7-lgb',
  'v8-torch',
  'v9-lgb',
  'v10-lgb',
  'v11-lgb',
  'v12-lgb',
  'v13-lgb',
  'v14-knn'],
 None,
 {})